In [1]:
import os
import sys
import re
import numpy as np
import pickle
from scipy.optimize import fmin
import multiprocessing as mp
import functools

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
# statmech library setup
sys.path.append('../../statmechlib')
from statmechlib.preprocessing import select_nodes, to_param_dict, to_param_list, insert_zero_params, rescale_manybody_params
from statmechlib.preprocessing import Trajectory, scale_configuration, pair_dist_cutoff, find_index
from statmechlib.forcefields import sd2_loss, utot_EAM_per_atom, utot_EAM_per_box, ftot_EAM, udif_print, u_core
from statmechlib.preprocessing import universal_eos
from statmechlib.preprocessing import pair_dist, force_targ, get_stats_EAM_per_atom, get_stats_EAM_per_box
from statmechlib.read_write import params_to_pickle

In [4]:
target_raw = '../data/target_raw'
target_proc = '../data/target_processed'
working = '../data/working'

In [5]:
# stats_file = 'stats_marinica' # 'stats_samples'
# target_file = 'target_marinica' # 'target_samples'
params_file = 'marinica_params'
# stats_file = 'stats_manyknots' # 'stats_samples'
# target_file = 'target_manyknots' # 'target_samples'
# stats_file = 'stats_manymd' # 'stats_samples'
# target_file = 'target_manymd' # 'target_samples'
stats_file = 'stats_manyall' # 'stats_samples'
target_file = 'target_manyall' # 'target_samples'
# stats_file = 'stats_everything' # 'stats_samples'
# target_file = 'target_everything' # 'target_samples'
stats_md_file = 'stats_onlymd' # 'stats_samples'
target_md_file = 'target_onlymd' # 'stats_samples'

In [6]:
with open(os.path.join(working, stats_file+'.pickle'), 'rb') as fi:
    stats_all = pickle.load(fi)

with open(os.path.join(working, target_file+'.pickle'), 'rb') as fi:
    targets = pickle.load(fi)
    
with open(os.path.join(working, stats_md_file+'.pickle'), 'rb') as fi:
    stats_md = pickle.load(fi)
    
with open(os.path.join(working, target_md_file+'.pickle'), 'rb') as fi:
    targets_md = pickle.load(fi)

with open(os.path.join(working, params_file + '.pickle'), 'rb') as fi:
    param_list = pickle.load(fi)  

In [7]:
def downselect(stats_inp, pair_knots, edens_knots):
    
    # find idices of knots
    pair_index = find_index(pair_knots, stats_inp['hyperparams']['pair'])
    edens_index = find_index(edens_knots, stats_inp['hyperparams']['edens'])
    
    # create boolean arrays with select indices set to True
    p_ix = np.array([True if i in pair_index else False for i in range(len(stats_inp['hyperparams']['pair']))])
    m_ix = np.array([True if i in edens_index else False for i in range(len(stats_inp['hyperparams']['edens']))])

    stats_out = select_nodes(stats_inp, p_ix, m_ix)
    
    return stats_out

In [8]:
# pair_knots = [2.22, 2.46, 2.5648975,  2.629795 ,  2.6946925,  2.8663175,  2.973045 ,
#         3.0797725,  3.5164725,  3.846445 ,  4.1764175,  4.700845 ,
#         4.8953   ,  5.089755 ,  5.3429525,  5.401695 ,  5.4604375]
# edens_knots = [ 2.22, 2.5,  2.6946925, 2.8663175, 3.1,  3.5,  4.5]

pair_knots = [2.22, 2.46, 2.5648975, 2.629795, 2.6946925, 2.8663175, 2.973045,
              3.0797725, 3.5164725, 3.846445, 4.1764175, 4.700845,
              4.8953, 5.089755, 5.3429525, 5.401695, 5.4604375, 5.58, 5.62]

# pair_knots = [2.22, 2.46, 2.5648975, 2.629795, 2.6946925, 2.8663175, 2.973045,
#               3.0797725, 3.5164725, 3.846445, 4.1764175, 4.700845,
#               4.8953, 5.18, 5.38, 5.58, 5.62]

#edens_knots = [2.5, 2.8663175000000001, 3.1, 3.5, 4.5]
#edens_knots = [2.5, 2.8663175000000001, 3.1, 3.5, 4.62]
edens_knots = [2.22, 2.5, 2.8663175000000001, 3.1, 3.5, 4.62]



In [9]:
stats = downselect(stats_all, pair_knots, edens_knots)
print(stats['hyperparams'])
stats_select_md = downselect(stats_md, pair_knots, edens_knots)
print(stats_select_md['hyperparams'])

{u'pair': [2.2200000000000002, 2.46, 2.5648974999999998, 2.6297950000000001, 2.6946924999999999, 2.8663175000000001, 2.9730449999999999, 3.0797724999999998, 3.5164724999999999, 3.8464450000000001, 4.1764175000000003, 4.7008450000000002, 4.8952999999999998, 5.0897550000000003, 5.3429525, 5.4016950000000001, 5.4604375000000003, 5.5800000000000001, 5.6200000000000001], u'edens': [2.2200000000000002, 2.5, 2.8663175000000001, 3.1000000000000001, 3.5, 4.6200000000000001]}
{u'pair': [2.2200000000000002, 2.46, 2.5648974999999998, 2.6297950000000001, 2.6946924999999999, 2.8663175000000001, 2.9730449999999999, 3.0797724999999998, 3.5164724999999999, 3.8464450000000001, 4.1764175000000003, 4.7008450000000002, 4.8952999999999998, 5.0897550000000003, 5.3429525, 5.4016950000000001, 5.4604375000000003, 5.5800000000000001, 5.6200000000000001], u'edens': [2.2200000000000002, 2.5, 2.8663175000000001, 3.1000000000000001, 3.5, 4.6200000000000001]}


In [10]:
targets['md'] = targets_md['md']
stats['md'] = stats_select_md['md']

In [11]:
# for key in sorted(targets.keys()):
#     for box, xyz, ene in zip(targets[key]['box'], targets[key]['xyz'], stats[key]['energy']):
#         n = len(xyz)
#         vol = np.linalg.det(box)
#         corr = float(n*n)/vol
#         ene.append([corr])

In [12]:
targets['eos_fcc']['weight'] = 0.0
targets['bain']['weight'] = 0.0
targets['eos']['weight'] = 0.0
targets['eos_bcc']['weight'] = 0.1
targets['relax']['weight'] = 0.0
#targets['liq_5000K']['weight'] = 0.1

In [13]:
targets['eos_bcc']['box'] = targets['eos_bcc']['box'][0:5]
targets['eos_bcc']['xyz'] = targets['eos_bcc']['xyz'][0:5]
targets['eos_bcc']['temp'] = targets['eos_bcc']['temp'][0:5]
targets['eos_bcc']['beta'] = targets['eos_bcc']['beta'][0:5]
targets['eos_bcc']['energy'] = targets['eos_bcc']['energy'][0:5]
targets['eos_bcc']['forces'] = targets['eos_bcc']['forces'][0:5]
stats['eos_bcc']['energy'] = stats['eos_bcc']['energy'][0:5]
stats['eos_bcc']['forces'] = stats['eos_bcc']['forces'][0:5]

In [14]:
[(key, targets[key]['weight']) for key in targets.keys()]

[('bcc_npt_langevin_3700K', 1.0),
 ('md', 1.0),
 ('vac_npt_langevin_2000K', 1.0),
 ('relax', 0.0),
 ('screw_111_npt_langevin_2000K', 1.0),
 ('bcc_npt_langevin_300K', 1.0),
 ('i111_npt_langevin_2000K', 1.0),
 ('eos', 0.0),
 ('fcc_npt_langevin_300K', 1.0),
 ('eos_fcc', 0.0),
 ('i110_npt_langevin_2000K', 1.0),
 ('liq_3700K', 1.0),
 ('liq_5000K', 1.0),
 ('eos_bcc', 0.1),
 ('bain', 0.0)]

In [23]:
start_params = []
# start_params.append([ -4.18353755e+00,  -9.63668936e-03,  0.0, -1.00171035e+02,
#          1.90025394e+01,   2.15938317e+01,  -1.39759833e+01,
#          2.16332289e+01,  -3.29542126e+00,   1.70455674e+00,
#          1.41347064e+00,  -9.02958785e-01,  -8.62309098e-01,
#          1.95964588e+00,  -8.70527088e-01,   3.22342700e-02,
#         -1.53866121e+00,   1.37095441e+00,  -4.32896107e+01,
#          4.64461212e+00,   3.23329113e-01,   5.82061842e-02, -0.1])
# start_params.append([ -4.36548916e+00,  -1.11867827e-02,  -1.94093020e+01,
#         -1.40195282e+02,   4.53864231e+01,   1.49756180e+01,
#         -1.36031385e+01,   2.21581200e+01,  -4.61501041e+00,
#          2.06360250e+00,   1.12795645e+00,  -8.01200744e-01,
#         -8.58426028e-01,   1.95860157e+00,  -8.68817546e-01,
#          2.43936831e-02,  -1.54555297e+00,   1.38005891e+00,
#         -5.22754243e+01,   3.98209114e+00,   3.07369702e-01,
#          5.51658454e-02,   1.58601447e+00])
# start_params.append([ -4.16739003e+00,  -4.97036785e-03,  -4.62426912e+02,
#          2.63469650e+02,   1.00253629e+01,   2.05151925e+01,
#         -1.36702712e+01,   2.29129977e+01,  -1.27210473e+01,
#          2.95533783e+00,   8.18470873e-01,  -7.89494754e-01,
#         -8.74455389e-01,   2.10177842e+00,  -9.22682795e-01,
#         -6.93852493e-02,  -1.52166575e+00,   1.40766925e+00,
#          1.52571934e+02,   3.37536873e-01,   6.89310740e-01,
#          4.87102227e-02,   2.79573955e+00])
# start_params.append([ -4.33954858e+00,  -1.02215197e-02,  0.0, -1.12590032e+02,
#          3.06702045e+01,   1.74951979e+01,  -1.33298120e+01,
#          2.13899957e+01,  -3.70881631e+00,   1.56452640e+00,
#          1.27789071e+00,  -8.54623702e-01,  -8.39818015e-01,
#          1.95990543e+00,  -8.75948596e-01,   1.81927625e-02,
#         -1.54683863e+00,   1.38614460e+00,  -4.28747460e+01,
#          4.18974818e+00,   1.56622590e-01,   5.72961538e-02,
#          3.46319317e+00])

# start_params.append([ -4.41712815e+00,  -7.57807965e-03, 0.0, 2.79276814e+02,
#          1.74479561e+02,  -6.59620942e+01,   3.53977481e+01,
#         -1.40546374e+01,   2.11913467e+01,  -4.95603366e+00,
#          8.26392820e-01,   1.26391280e+00,  -9.48799563e-01,
#         -7.79099318e-01,   2.00268261e+00,  -8.90495881e-01,
#         -8.59210993e-03,  -1.54948191e+00,   1.39577855e+00,
#          2.43904610e+02,   3.47694754e+00,  -3.14999583e-01,
#          6.33069119e-02,   5.60287637e+00])

# start_params.append([-4.48347382e+00,  -7.78079006e-03,   2.92055760e+02,
#          1.84809430e+02,  -6.18705307e+01,   3.27735461e+01,
#         -1.36588262e+01,   2.11547368e+01,  -5.45394162e+00,
#          8.02998352e-01,   1.21949599e+00,  -9.43034331e-01,
#         -7.71285316e-01,   2.00564540e+00,  -8.93039729e-01,
#         -9.92574423e-03,  -1.55106037e+00,   1.39898785e+00,
#          2.54912062e+02,   3.19484582e+00,  -3.49947883e-01,
#          6.32970386e-02,   4.13612869e+00])

# start_params.append([ -4.41712815e+00,  -7.57807965e-03, 0.0, 2.79276814e+02,
#          1.74479561e+02,  -6.59620942e+01,   3.53977481e+01,
#         -1.40546374e+01,   2.11913467e+01,  -4.95603366e+00,
#          8.26392820e-01,   1.26391280e+00,  -9.48799563e-01,
#         -7.79099318e-01,   2.00268261e+00,  -8.90495881e-01,
#         -8.59210993e-03,  -1.54948191e+00,   1.39577855e+00,
#          2.43904610e+02,   3.47694754e+00,  -3.14999583e-01,
#          6.33069119e-02])

# start_params.append([ -3.09187534e+00,   1.19622206e-04,  -5.67875917e+02,
#          3.21802084e+02,  -4.71317094e+02,   3.98296604e+02,
#         -1.13270858e+02,   6.03114401e+00,   1.48067908e+01,
#         -1.57531660e+01,   7.80863462e+00,  -2.99246651e+00,
#          7.33596451e-01,  -9.50794219e-01,   1.94186078e+00,
#         -8.83596676e-01,  -1.33608784e-01,  -1.46694544e+00,
#          1.42447434e+00,   7.53865380e+01,   3.29733034e-01,
#          2.18327852e+00,   6.63152141e-02, 0.0])

# start_params.append([ -2.95016477e+00,   3.78177969e-04,  -5.21095611e+02,
#          3.09845244e+02,  -4.69222440e+02,   3.95186037e+02,
#         -1.11630659e+02,   5.36915127e+00,   1.52984702e+01,
#         -1.54915170e+01,   7.53107481e+00,  -2.98591742e+00,
#          7.55346307e-01,  -1.00678488e+00,   1.96634582e+00,
#         -8.71560927e-01,  -1.41820832e-01,  -1.46508000e+00,
#          1.42936365e+00,   7.23805795e+01,   0.0, 9.18071460e-01,
#          2.04259992e+00,   6.28575567e-02,   7.62804667e-03])

# start_params.append([ -3.27882058e+00,  -9.77681860e-04,  -5.95486537e+02,
#          3.42401535e+02,  -4.15497479e+02,   3.71316746e+02,
#         -1.07274610e+02,  -2.93282898e+00,   1.51298572e+01,
#         -1.37454674e+01,   8.16724633e+00,  -3.16850352e+00,
#          8.74607042e-01,  -1.07878768e+00,   1.97939820e+00,
#         -8.26149646e-01,  -1.62437297e-01,  -1.45694910e+00,
#          1.42153527e+00,   1.29203135e+02,  -9.25284676e+00,
#          2.63967417e+00,   2.06410900e+00,   6.03258240e-02*2])

# start_params.append([ -3.56709315e+00,  -2.97358686e-03,  -4.37632666e+02,
#          3.35095381e+02,  -2.95083648e+02,   2.94263473e+02,
#         -8.57731610e+01,  -1.62036228e+01,   1.30838141e+01,
#         -6.46551376e+00,   8.01826587e+00,  -3.58786095e+00,
#          1.25735987e+00,  -1.21627097e+00,   2.04033545e+00,
#         -8.04702913e-01,  -1.92666480e-01,  -1.44083371e+00,
#          1.41816098e+00,   1.70360405e+02,  -1.89070431e+01,
#          7.47139804e+00,   1.20540194e+00,   1.34588181e-01, 0.0])

# start_params.append([ -3.89054208e+00,  -2.99469508e-03,  -7.60325091e+02,
#          2.25922421e+02,   4.31682139e+01,  -2.00879587e+01,
#          3.15977299e+01,  -1.41216383e+01,   1.40729549e+01,
#         -2.29741069e-01,   5.66020784e-01,   9.50813370e-01,
#         -7.07877506e-01,  -6.33885976e-01,   2.11514130e+00,
#         -1.07084535e+00,  -1.99471358e-01,  -1.53976066e+00,
#          1.54749579e+00,   1.94668273e+02,  -1.93218649e+00,
#          4.87330211e+00,  -4.95019886e-01,   1.54561460e-01])

# start_params.append([ -3.01252922e+00,   3.34774026e-03,  -3.63245948e+02,
#          7.08473344e+01,   5.18269140e+00,  -4.21852665e+01,
#          5.03986439e+01,  -3.49299323e+01,   9.39050841e+00,
#          7.10916965e+00,   2.53141800e+00,  -1.27714028e-01,
#         -8.13152443e-01,  -5.45294030e-01,   2.19662624e+00,
#         -1.03021233e+00,  -2.37376783e-01,  -1.54945600e+00,
#          1.51410989e+00,   8.93873263e+01,  -2.44415218e+01,
#          1.44237601e+01,  -2.48517486e-01,   1.57735701e-01,
#         0.0])

# start_params.append([ -2.76762846e+00,   1.89330096e-03,  -3.78969507e+02,
#          4.97375946e+01,   5.61080362e+01,  -8.13991417e+01,
#          6.18213043e+01,  -3.36881958e+01,   9.64679581e+00,
#          6.37021438e+00,   2.56205745e+00,  -6.89271288e-02,
#         -8.28256696e-01,  -5.90663693e-01,   2.19738636e+00,
#         -9.78519868e-01,  -2.34054246e-01,  -1.56404102e+00,
#          1.50934562e+00,   1.25199350e+02,  -2.58933860e+01,
#          1.60206690e+01,  -2.46344691e-01,   1.98323959e-01,
#         0.0])

# start_params.append([ -2.96336623e+00,   9.35841772e-04,  -4.69405427e+02,
#          6.56489326e+01,   6.59098372e+01,  -6.95558862e+01,
#          5.05321941e+01,  -2.68901225e+01,   6.12983979e+00,
#          8.40257564e+00,   2.03599185e+00,   1.44655457e-01,
#         -8.07626370e-01,  -6.77900254e-01,   2.19493850e+00,
#         -9.02854774e-01,  -2.35346587e-01,  -1.56947636e+00,
#          1.49891405e+00,   1.54692423e+02,  -1.84128239e+01,
#          1.40416342e+01,  -4.74336808e-01,   2.07514499e-01])

# start_params.append([ -2.83157185e+00,   8.39115358e-04,  -4.21330968e+02,
#          5.62354559e+01,   6.55868693e+01,  -7.39097694e+01,
#          5.32753168e+01,  -2.90768080e+01,   9.73480693e+00,
#          5.86938247e+00,   2.40344261e+00,   1.33807130e-01,
#         -7.34188649e-01,  -8.53691403e-01,   2.20105517e+00,
#         -7.61586871e-01,  -2.42532670e-01,  -1.58457873e+00,
#          1.47655687e+00,   0.0, 1.48755630e+02,  0.0, -1.98109911e+01,
#          1.44803287e+01,  -1.17489342e-01,   2.06651900e-01])

# start_params.append([ -3.91274686e+00,  -5.02814282e-03,  -3.60607144e+02,
#          3.08180837e+02,  -2.45731624e+02,   2.57711860e+02,
#         -7.57560376e+01,  -3.26396342e+01,   1.25979333e+01,
#         -3.17982854e+00,   7.88108320e+00,  -3.46868286e+00,
#          1.29424331e+00,  -1.31629778e+00,   2.05422384e+00,
#         -8.33747039e-01,  -1.75108086e-01,  -1.43404985e+00,
#          1.45403961e+00,   1.43868098e+02,  -2.72551797e+01,
#          8.05592823e+00,   1.03649030e+00,   1.04857599e-01,
#         -4.20237149e+01])

# start_params.append([ -3.34519702e+00,   7.66822271e-04,  -4.03553412e+02,
#          1.55282185e+01,   2.90516401e+01,  -6.23087513e+01,
#          8.48184009e+01, -3.48806112e+01,   9.13550274e+00,
#          5.96096071e+00,   2.54062374e+00,   2.39873080e-01,
#         -7.19239652e-01,  -1.04267291e+00,   2.29366373e+00,
#         -7.05206149e-01,  -2.72279799e-01,  -1.55954882e+00,
#          1.45964251e+00,  -2.01431222e+02,   3.24297105e+01,
#          3.81664135e+01,  -2.18948938e+01,   1.02484895e+01,
#          2.20300623e-01,   1.13874983e-01])

# start_params.append([ -4.65804603e+00,  -7.56457588e-03,  -1.68777520e+02,
#          1.56052349e+02,   1.42649908e+01,  -4.55941009e+00,
#          1.97613340e+01,   4.84204936e+01,   6.49466770e+00,
#         -6.62233324e+00,  -2.16547494e+00,   1.30932417e+00,
#         -8.33281480e-01,  -8.32333597e-01,   2.09417158e+00,
#         -6.19566076e-01,  -9.53112547e-02,  -1.49756931e+00,
#          1.27167940e+00,   -1.05537460e-02,   1.06186365e+02,   2.86689290e+01,
#         -2.47374985e+00,  -1.24252596e+00,   1.65373019e-01])

# start_params.append([
#     -4.96571997, -0.00970695776,
#     -4.23764410e+03,   9.82966281e+01,  -6.09610499e+01,
#         -1.41310061e+01,   4.09003482e+01,   4.59147811e+01,
#          1.69148405e+01,  -1.08920404e+01,  -2.15512880e+00,
#          1.19928506e+00,  -9.64477377e-01,  -5.06943698e-01,
#          1.54791512e+00,  -6.82398422e-01,   1.58195979e-02,
#         -5.69663710e-01,   5.77918066e-01,
#     -1337.64316,25.3825479,28.1342191,
#     -1.1392692,-1.62929262,0.166534929 
# ])

# start_params.append([
#         -4.20657287, -0.00479083415,
#     -4286.62319,139.452507,29.1473879,-10.8844243,
#     15.9102238,48.6110415,7.3059187,-8.24225202,-1.76541035,
#     1.69386336,-1.23281961,-0.791007042,1.98078659,-0.492223582,
#     -0.0464721217,-1.47436944,1.19244103, 0.0, 0.0,
#         -3037.16289, 125.775067, 32.7634816,
#         -1.80274854, -1.77552231, 0.210521327
# ])

# start_params.append([ -4.19182098e+00,  -4.55515592e-03,  -3.43969103e+03,
#          1.36126472e+02,   2.43326975e+01,  -7.74316138e+00,
#          1.48801992e+01,   4.82819864e+01,   7.41179369e+00,
#         -8.19055688e+00,  -1.75410852e+00,   1.69354046e+00,
#         -1.23660713e+00,  -7.88958753e-01,   1.98062027e+00,
#         -4.91303949e-01,  -4.63747685e-02,  -1.47566087e+00,
#          1.19247036e+00,  -6.88108179e-04,  -7.11551613e-05,
#         -2.42764281e+03,   1.24089957e+02,   3.27326312e+01,
#         -1.74063696e+00,  -1.78165722e+00,   2.09403067e-01])

start_params.append([ -4.25079261e+00,  -3.83398788e-03,   5.31614359e+03,
         9.70449455e+01,  -3.21921326e+01,   1.42834686e+01,
         1.03249791e+01,   4.77039657e+01,   7.21865085e+00,
        -7.61392045e+00,  -2.04274697e+00,   1.84772949e+00,
        -1.26953164e+00,  -8.02360677e-01,   1.98259078e+00,
        -4.92179482e-01,  -4.91531474e-02,  -1.47125886e+00,
         1.19265777e+00,   6.51742613e-04,  -8.76870229e-04,
         4.46749225e+03,   6.65943448e+01,   3.17786714e+01,
        -1.59740549e+00,  -1.78010434e+00,   2.02988349e-01])

multi_pars = start_params
print(multi_pars)

[[-4.19182098, -0.00455515592, -3439.69103, 136.126472, 24.3326975, -7.74316138, 14.8801992, 48.2819864, 7.41179369, -8.19055688, -1.75410852, 1.69354046, -1.23660713, -0.788958753, 1.98062027, -0.491303949, -0.0463747685, -1.47566087, 1.19247036, -0.000688108179, -7.11551613e-05, -2427.64281, 124.089957, 32.7326312, -1.74063696, -1.78165722, 0.209403067]]


In [24]:
def optimize_EAM_mp(pars, targets, stats, utot_func):
    
    output = fmin(sd2_loss, pars, args=(targets, stats, utot_EAM_per_atom, None, 0.05, 1), maxiter=100000, maxfun=100000, disp=0, full_output=1,ftol=1e-6)

    return tuple([output[1], output[0]])

In [ ]:
params_output = []

pool = mp.Pool()

for ieam in range(1):#5, len(stats_opts[it]['hyperparams'])):

    get_sd = functools.partial(sd2_loss, targets=targets, stats=stats, utot_func=utot_EAM_per_atom, ftot_func=None, dl=0.05, verbose=1)

    get_opt = functools.partial(optimize_EAM_mp, targets=targets, stats=stats, utot_func=utot_EAM_per_atom)

    # initial ordering
    print('Initial params:', multi_pars[-1])
    
    #distances = pool.map(get_sd, multi_pars)
    
    distances = [get_sd(multi_pars[-1])]
    
    optimal_params = zip(distances, multi_pars[-1:])
    best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
    m_pars = [p[1] for p in best_params]

    print('Best params:', best_params)
    print('ieam:', ieam)
    #m_pars = multi_pars

    for i in range(50):
        #optimal_params = pool.map(get_opt, m_pars)
        optimal_params = [get_opt(m_pars)]
        best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
        m_pars = [p[1] for p in best_params]
        
        print("Iteration {}, best params: {}".format(i, best_params))

    print('Final Best params:', best_params)
    
    params_output.append(best_params)

pool.close()
pool.join()

('Initial params:', [-4.19182098, -0.00455515592, -3439.69103, 136.126472, 24.3326975, -7.74316138, 14.8801992, 48.2819864, 7.41179369, -8.19055688, -1.75410852, 1.69354046, -1.23660713, -0.788958753, 1.98062027, -0.491303949, -0.0463747685, -1.47566087, 1.19247036, -0.000688108179, -7.11551613e-05, -2427.64281, 124.089957, 32.7326312, -1.74063696, -1.78165722, 0.209403067])
loss 1.50353638919e-06 1.50353638919e-06 0.0
('Best params:', [(1.5035363891885519e-06, [-4.19182098, -0.00455515592, -3439.69103, 136.126472, 24.3326975, -7.74316138, 14.8801992, 48.2819864, 7.41179369, -8.19055688, -1.75410852, 1.69354046, -1.23660713, -0.788958753, 1.98062027, -0.491303949, -0.0463747685, -1.47566087, 1.19247036, -0.000688108179, -7.11551613e-05, -2427.64281, 124.089957, 32.7326312, -1.74063696, -1.78165722, 0.209403067])])
('ieam:', 0)
loss 1.50353638919e-06 1.50353638919e-06 0.0
loss 0.00110495244455 0.00110495244455 0.0
loss 4.86409826301e-06 4.86409826301e-06 0.0
loss 1.51218010224e-06 1.512

loss 1.65270433265e-05 1.65270433265e-05 0.0
loss 5.00668383908e-06 5.00668383908e-06 0.0
loss 2.13129861562e-05 2.13129861562e-05 0.0
loss 4.27357979238e-06 4.27357979238e-06 0.0
loss 1.22618162752e-05 1.22618162752e-05 0.0
loss 1.54261220054e-05 1.54261220054e-05 0.0
loss 4.18763162534e-06 4.18763162534e-06 0.0
loss 1.40420546448e-05 1.40420546448e-05 0.0
loss 4.11287320381e-06 4.11287320381e-06 0.0
loss 1.31735406877e-05 1.31735406877e-05 0.0
loss 4.12969113955e-06 4.12969113955e-06 0.0
loss 1.19844610937e-05 1.19844610937e-05 0.0
loss 3.63498449892e-06 3.63498449892e-06 0.0
loss 1.21523143801e-05 1.21523143801e-05 0.0
loss 3.56072870613e-06 3.56072870613e-06 0.0
loss 9.44712090714e-06 9.44712090714e-06 0.0
loss 1.13532101147e-05 1.13532101147e-05 0.0
loss 3.3434947709e-06 3.3434947709e-06 0.0
loss 1.03610392704e-05 1.03610392704e-05 0.0
loss 3.44560136045e-06 3.44560136045e-06 0.0
loss 8.23628851068e-06 8.23628851068e-06 0.0
loss 3.19545024455e-06 3.19545024455e-06 0.0
loss 7.29650

loss 1.51063946277e-06 1.51063946277e-06 0.0
loss 1.53000133086e-06 1.53000133086e-06 0.0
loss 1.5449709218e-06 1.5449709218e-06 0.0
loss 1.50895656999e-06 1.50895656999e-06 0.0
loss 1.53270588803e-06 1.53270588803e-06 0.0
loss 1.51016064853e-06 1.51016064853e-06 0.0
loss 1.5204922851e-06 1.5204922851e-06 0.0
loss 1.53441959461e-06 1.53441959461e-06 0.0
loss 1.5088732895e-06 1.5088732895e-06 0.0
loss 1.5232741872e-06 1.5232741872e-06 0.0
loss 1.53345336906e-06 1.53345336906e-06 0.0
loss 1.50851949243e-06 1.50851949243e-06 0.0
loss 1.52958944909e-06 1.52958944909e-06 0.0
loss 1.50856524397e-06 1.50856524397e-06 0.0
loss 1.52339710409e-06 1.52339710409e-06 0.0
loss 1.52595364733e-06 1.52595364733e-06 0.0
loss 1.50865800049e-06 1.50865800049e-06 0.0
loss 1.52814097349e-06 1.52814097349e-06 0.0
loss 1.50804034514e-06 1.50804034514e-06 0.0
loss 1.52333187823e-06 1.52333187823e-06 0.0
loss 1.50850737356e-06 1.50850737356e-06 0.0
loss 1.52636287082e-06 1.52636287082e-06 0.0
loss 1.50814232944

loss 1.50362230423e-06 1.50362230423e-06 0.0
loss 1.50382283151e-06 1.50382283151e-06 0.0
loss 1.50362337156e-06 1.50362337156e-06 0.0
loss 1.50387468656e-06 1.50387468656e-06 0.0
loss 1.50361747464e-06 1.50361747464e-06 0.0
loss 1.50379112146e-06 1.50379112146e-06 0.0
loss 1.50386819558e-06 1.50386819558e-06 0.0
loss 1.5036077661e-06 1.5036077661e-06 0.0
loss 1.50378854006e-06 1.50378854006e-06 0.0
loss 1.50387333273e-06 1.50387333273e-06 0.0
loss 1.50360601962e-06 1.50360601962e-06 0.0
loss 1.50377308118e-06 1.50377308118e-06 0.0
loss 1.50383524048e-06 1.50383524048e-06 0.0
loss 1.50360829431e-06 1.50360829431e-06 0.0
loss 1.50388910805e-06 1.50388910805e-06 0.0
loss 1.50360197686e-06 1.50360197686e-06 0.0
loss 1.50386568402e-06 1.50386568402e-06 0.0
loss 1.5036046473e-06 1.5036046473e-06 0.0
loss 1.50372656779e-06 1.50372656779e-06 0.0
loss 1.50381325842e-06 1.50381325842e-06 0.0
loss 1.50360631061e-06 1.50360631061e-06 0.0
loss 1.50381651537e-06 1.50381651537e-06 0.0
loss 1.5036055

loss 1.50355202814e-06 1.50355202814e-06 0.0
loss 1.50354521028e-06 1.50354521028e-06 0.0
loss 1.50354445686e-06 1.50354445686e-06 0.0
loss 1.50355508104e-06 1.50355508104e-06 0.0
loss 1.50354438301e-06 1.50354438301e-06 0.0
loss 1.50354531173e-06 1.50354531173e-06 0.0
loss 1.5035420958e-06 1.5035420958e-06 0.0
loss 1.50354266597e-06 1.50354266597e-06 0.0
loss 1.50354696486e-06 1.50354696486e-06 0.0
loss 1.50354169577e-06 1.50354169577e-06 0.0
loss 1.5035416728e-06 1.5035416728e-06 0.0
loss 1.50354059757e-06 1.50354059757e-06 0.0
loss 1.50354595381e-06 1.50354595381e-06 0.0
loss 1.50353879389e-06 1.50353879389e-06 0.0
loss 1.50353999242e-06 1.50353999242e-06 0.0
loss 1.50354423665e-06 1.50354423665e-06 0.0
loss 1.50354591875e-06 1.50354591875e-06 0.0
loss 1.50354894466e-06 1.50354894466e-06 0.0
loss 1.50354166606e-06 1.50354166606e-06 0.0
loss 1.50354880661e-06 1.50354880661e-06 0.0
loss 1.50354154915e-06 1.50354154915e-06 0.0
loss 1.50354026378e-06 1.50354026378e-06 0.0
loss 1.5035387

...

loss 1.49027914275e-06 1.49027914275e-06 0.0
loss 1.49027878937e-06 1.49027878937e-06 0.0
loss 1.49027881565e-06 1.49027881565e-06 0.0
loss 1.49027885853e-06 1.49027885853e-06 0.0
loss 1.49027867794e-06 1.49027867794e-06 0.0
loss 1.49027795595e-06 1.49027795595e-06 0.0
loss 1.49027860067e-06 1.49027860067e-06 0.0
loss 1.49027887332e-06 1.49027887332e-06 0.0
loss 1.49027841613e-06 1.49027841613e-06 0.0
loss 1.49027805548e-06 1.49027805548e-06 0.0
loss 1.49027818343e-06 1.49027818343e-06 0.0
loss 1.49027795507e-06 1.49027795507e-06 0.0
loss 1.49027700137e-06 1.49027700137e-06 0.0
loss 1.4902778127e-06 1.4902778127e-06 0.0
loss 1.49027782533e-06 1.49027782533e-06 0.0
loss 1.49027770927e-06 1.49027770927e-06 0.0
loss 1.49027746931e-06 1.49027746931e-06 0.0
loss 1.49027734552e-06 1.49027734552e-06 0.0
loss 1.49027759465e-06 1.49027759465e-06 0.0
loss 1.49027701789e-06 1.49027701789e-06 0.0
loss 1.49027732418e-06 1.49027732418e-06 0.0
loss 1.49027696016e-06 1.49027696016e-06 0.0
loss 1.49027

loss 1.49025337767e-06 1.49025337767e-06 0.0
loss 1.4902531126e-06 1.4902531126e-06 0.0
loss 1.49025279374e-06 1.49025279374e-06 0.0
loss 1.49025213384e-06 1.49025213384e-06 0.0
loss 1.49024986776e-06 1.49024986776e-06 0.0
loss 1.49025220658e-06 1.49025220658e-06 0.0
loss 1.49025181988e-06 1.49025181988e-06 0.0
loss 1.49025197932e-06 1.49025197932e-06 0.0
loss 1.49025137899e-06 1.49025137899e-06 0.0
loss 1.49025156698e-06 1.49025156698e-06 0.0
loss 1.49025297955e-06 1.49025297955e-06 0.0
loss 1.49025152579e-06 1.49025152579e-06 0.0
loss 1.4902512798e-06 1.4902512798e-06 0.0
loss 1.49025052511e-06 1.49025052511e-06 0.0
loss 1.49025106823e-06 1.49025106823e-06 0.0
loss 1.49025082127e-06 1.49025082127e-06 0.0
loss 1.490249798e-06 1.490249798e-06 0.0
loss 1.49024754069e-06 1.49024754069e-06 0.0
loss 1.49024991441e-06 1.49024991441e-06 0.0
loss 1.49024970036e-06 1.49024970036e-06 0.0
loss 1.49024925987e-06 1.49024925987e-06 0.0
loss 1.49024877094e-06 1.49024877094e-06 0.0
loss 1.49024818571

loss 1.49021210114e-06 1.49021210114e-06 0.0
loss 1.490211297e-06 1.490211297e-06 0.0
loss 1.49020797582e-06 1.49020797582e-06 0.0
loss 1.49020974593e-06 1.49020974593e-06 0.0
loss 1.49021035281e-06 1.49021035281e-06 0.0
loss 1.4902120395e-06 1.4902120395e-06 0.0
loss 1.49020580111e-06 1.49020580111e-06 0.0
loss 1.49020198454e-06 1.49020198454e-06 0.0
loss 1.49020752933e-06 1.49020752933e-06 0.0
loss 1.4902084554e-06 1.4902084554e-06 0.0
loss 1.49020564303e-06 1.49020564303e-06 0.0
loss 1.49020770774e-06 1.49020770774e-06 0.0
loss 1.49020642617e-06 1.49020642617e-06 0.0
loss 1.49020765065e-06 1.49020765065e-06 0.0
loss 1.49020412317e-06 1.49020412317e-06 0.0
loss 1.49020465432e-06 1.49020465432e-06 0.0
loss 1.49020579903e-06 1.49020579903e-06 0.0
loss 1.49020284414e-06 1.49020284414e-06 0.0
loss 1.49020597081e-06 1.49020597081e-06 0.0
loss 1.49020671633e-06 1.49020671633e-06 0.0
loss 1.49020798887e-06 1.49020798887e-06 0.0
loss 1.49020973901e-06 1.49020973901e-06 0.0
loss 1.49020653288

loss 1.49011547165e-06 1.49011547165e-06 0.0
loss 1.49011968669e-06 1.49011968669e-06 0.0
loss 1.49011403349e-06 1.49011403349e-06 0.0
loss 1.4901115111e-06 1.4901115111e-06 0.0
loss 1.4901117331e-06 1.4901117331e-06 0.0
loss 1.49012348624e-06 1.49012348624e-06 0.0
loss 1.49011134464e-06 1.49011134464e-06 0.0
loss 1.49011245629e-06 1.49011245629e-06 0.0
loss 1.49010838128e-06 1.49010838128e-06 0.0
loss 1.49011288832e-06 1.49011288832e-06 0.0
loss 1.49010676797e-06 1.49010676797e-06 0.0
loss 1.49012080034e-06 1.49012080034e-06 0.0
loss 1.49011103725e-06 1.49011103725e-06 0.0
loss 1.49010781472e-06 1.49010781472e-06 0.0
loss 1.49011159053e-06 1.49011159053e-06 0.0
loss 1.49010878784e-06 1.49010878784e-06 0.0
loss 1.49010470217e-06 1.49010470217e-06 0.0
loss 1.49010174682e-06 1.49010174682e-06 0.0
loss 1.490107301e-06 1.490107301e-06 0.0
loss 1.49010138312e-06 1.49010138312e-06 0.0
loss 1.49009668062e-06 1.49009668062e-06 0.0
loss 1.49009983525e-06 1.49009983525e-06 0.0
loss 1.49010329018

loss 1.48999119236e-06 1.48999119236e-06 0.0
loss 1.49000031486e-06 1.49000031486e-06 0.0
loss 1.49000511577e-06 1.49000511577e-06 0.0
loss 1.48999100078e-06 1.48999100078e-06 0.0
loss 1.4899955653e-06 1.4899955653e-06 0.0
loss 1.48999498341e-06 1.48999498341e-06 0.0
loss 1.48998668729e-06 1.48998668729e-06 0.0
loss 1.48999852243e-06 1.48999852243e-06 0.0
loss 1.48998762945e-06 1.48998762945e-06 0.0
loss 1.48998939834e-06 1.48998939834e-06 0.0
loss 1.48999027793e-06 1.48999027793e-06 0.0
loss 1.48998534881e-06 1.48998534881e-06 0.0
loss 1.48998515227e-06 1.48998515227e-06 0.0
loss 1.48999462409e-06 1.48999462409e-06 0.0
loss 1.48999219906e-06 1.48999219906e-06 0.0
loss 1.4899903866e-06 1.4899903866e-06 0.0
loss 1.48998375139e-06 1.48998375139e-06 0.0
loss 1.48999545962e-06 1.48999545962e-06 0.0
loss 1.48997726452e-06 1.48997726452e-06 0.0
loss 1.48997774933e-06 1.48997774933e-06 0.0
loss 1.49000084401e-06 1.49000084401e-06 0.0


In [17]:
# params_output = [ -4.72546533e+00,  -6.97068121e-03,  -3.51290250e+02,
#          1.63175272e+02,   9.43598046e+00,  -3.25684355e+00,
#          2.30446047e+01,   4.06678582e+01,   7.56509137e+00,
#         -7.51663487e+00,  -1.59146529e+00,   1.14098894e+00,
#         -8.25274736e-01,  -8.09954101e-01,   2.09984210e+00,
#         -6.52067950e-01,  -8.56530962e-02,  -1.49919134e+00,
#          1.27499075e+00,   1.07226915e+02,   2.36918896e+01,
#         -1.29592031e+00,  -1.49967198e+00,   2.14664790e-01]
# params_output = [[ -4.65804603e+00,  -7.56457588e-03,  -1.68777520e+02,
#          1.56052349e+02,   1.42649908e+01,  -4.55941009e+00,
#          1.97613340e+01,   4.84204936e+01,   6.49466770e+00,
#         -6.62233324e+00,  -2.16547494e+00,   1.30932417e+00,
#         -8.33281480e-01,  -8.32333597e-01,   2.09417158e+00,
#         -6.19566076e-01,  -9.53112547e-02,  -1.49756931e+00,
#          1.27167940e+00,   1.06853821e+02,   2.74234479e+01,
#         -1.26300179e+00,  -1.66378666e+00,   2.24848394e-01]]

# params_output = [[ -4.96571997e+00,  -9.70695776e-03,  -2.69597001e+03,
#          1.06172942e+02,  -9.45431278e+01,   3.88799435e+01,
#          8.37612190e+00,   5.83170234e+01,   7.58236573e+00,
#         -7.89909608e+00,  -2.26521289e+00,   1.17286424e+00,
#         -8.71880389e-01,  -8.53217217e-01,   2.11019782e+00,
#         -6.07750055e-01,  -1.50403641e-01,  -1.45924396e+00,
#          1.28914484e+00,  -1.33764316e+03,   2.53825479e+01,
#          2.81342191e+01,  -1.13926920e+00,  -1.62929262e+00,
#          1.66534929e-01]]

# params_output = [
#     -4.96571997, -0.00970695776,
#     -4.23764410e+03,   9.82966281e+01,  -6.09610499e+01,
#         -1.41310061e+01,   4.09003482e+01,   4.59147811e+01,
#          1.69148405e+01,  -1.08920404e+01,  -2.15512880e+00,
#          1.19928506e+00,  -9.64477377e-01,  -5.06943698e-01,
#          1.54791512e+00,  -6.82398422e-01,   1.58195979e-02,
#         -5.69663710e-01,   5.77918066e-01,
#     -1337.64316,25.3825479,28.1342191,
#     -1.1392692,-1.62929262,0.166534929 
# ]
params_output = [[ -4.19182098e+00,  -4.55515592e-03,  -3.43969103e+03,
         1.36126472e+02,   2.43326975e+01,  -7.74316138e+00,
         1.48801992e+01,   4.82819864e+01,   7.41179369e+00,
        -8.19055688e+00,  -1.75410852e+00,   1.69354046e+00,
        -1.23660713e+00,  -7.88958753e-01,   1.98062027e+00,
        -4.91303949e-01,  -4.63747685e-02,  -1.47566087e+00,
         1.19247036e+00,  -6.88108179e-04,  -7.11551613e-05,
        -2.42764281e+03,   1.24089957e+02,   3.27326312e+01,
        -1.74063696e+00,  -1.78165722e+00,   2.09403067e-01]]

print(params_output)

[[-4.19182098, -0.00455515592, -3439.69103, 136.126472, 24.3326975, -7.74316138, 14.8801992, 48.2819864, 7.41179369, -8.19055688, -1.75410852, 1.69354046, -1.23660713, -0.788958753, 1.98062027, -0.491303949, -0.0463747685, -1.47566087, 1.19247036, -0.000688108179, -7.11551613e-05, -2427.64281, 124.089957, 32.7326312, -1.74063696, -1.78165722, 0.209403067]]


In [18]:
# convert lists of optimal parameters to dictionaries
params_dicts = []
for params in params_output:
    params_dicts.append(to_param_dict(params, stats['hyperparams']))

In [19]:
params_dicts

[{'hyperparams': {u'edens': [2.2200000000000002,
    2.5,
    2.8663175000000001,
    3.1000000000000001,
    3.5,
    4.6200000000000001],
   u'pair': [2.2200000000000002,
    2.46,
    2.5648974999999998,
    2.6297950000000001,
    2.6946924999999999,
    2.8663175000000001,
    2.9730449999999999,
    3.0797724999999998,
    3.5164724999999999,
    3.8464450000000001,
    4.1764175000000003,
    4.7008450000000002,
    4.8952999999999998,
    5.0897550000000003,
    5.3429525,
    5.4016950000000001,
    5.4604375000000003,
    5.5800000000000001,
    5.6200000000000001]},
  'params': {'edens': [-2427.64281,
    124.089957,
    32.7326312,
    -1.74063696,
    -1.78165722,
    0.209403067],
   'embed': [-4.19182098, -0.00455515592],
   'lrcorr': [],
   'pair': [-3439.69103,
    136.126472,
    24.3326975,
    -7.74316138,
    14.8801992,
    48.2819864,
    7.41179369,
    -8.19055688,
    -1.75410852,
    1.69354046,
    -1.23660713,
    -0.788958753,
    1.98062027,
    -0.491303

In [20]:
file_name = os.path.join(working, "params_out.pickle")

for params in params_dicts:
    params_to_pickle(params, file_name)

In [21]:
with open(os.path.join(working, 'params_out' + '.pickle'), 'rb') as fi:
    retreived_params = pickle.load(fi)  

In [22]:
retreived_params

[{'hyperparams': {u'edens': [2.5,
    2.8663175000000001,
    3.1000000000000001,
    3.5,
    4.5],
   u'pair': [2.2200000000000002,
    2.46,
    2.5648974999999998,
    2.6297950000000001,
    2.6946924999999999,
    2.8663175000000001,
    2.9730449999999999,
    3.0797724999999998,
    3.5164724999999999,
    3.8464450000000001,
    4.1764175000000003,
    4.7008450000000002,
    4.8952999999999998,
    5.0897550000000003,
    5.3429525,
    5.4016950000000001,
    5.4604375000000003]},
  'params': {'edens': [106.853821,
    27.4234479,
    -1.26300179,
    -1.66378666,
    0.224848394],
   'embed': [-4.65804603, -0.00756457588],
   'lrcorr': [],
   'pair': [-168.77752,
    156.052349,
    14.2649908,
    -4.55941009,
    19.761334,
    48.4204936,
    6.4946677,
    -6.62233324,
    -2.16547494,
    1.30932417,
    -0.83328148,
    -0.832333597,
    2.09417158,
    -0.619566076,
    -0.0953112547,
    -1.49756931,
    1.2716794]}},
 {'hyperparams': {u'edens': [2.2200000000000002,